# Assignment 4 - Deep Learning
## Due Monday, April 9, 2018



In [2]:
## Tips:
## initially use fewer filters and gradually increase and monitor the error rate to see how it is varying.
## It is always a tradeoff between speed and accuracy. But there is several to-do`s and never-do`s.
## Kernel(filter) size: smaller + deeper = better. Deeper - better up to some level. Wider - better, but at some level there is an accuracy saturation, and computations grow up quadratically.

## Part A - Deep Learning model (40 points)
## 1. Apply a Deep Learning model to your project data (if possible). 
## 2. Validate the accuracy.
## The Deep Learning model can be a CNN, RNN, Autoencoder, Variational autoencoder (VAE), Restricted Boltzmann machine (RBM), Deep belief network (DBN) or Generative Model. 
## It cannot be a simple multilayer perceptron (MLP).


In [3]:
from keras.datasets import cifar10 # subroutines for fetching the CIFAR-10 dataset
from keras.models import Model # basic class for specifying and training a neural network
from keras.layers import Input, Convolution2D, MaxPooling2D, Dense, Dropout, Activation, Flatten
from keras.utils import np_utils # utilities for one-hot encoding of ground truth values
import numpy as np

Using TensorFlow backend.


## Configuration of Neural Network

In [5]:
batch_size = 32 # in each iteration, we consider 32 training examples at once
num_epochs = 2 # we iterate 200 times over the entire training set
kernel_size = 3 # we will use 3x3 kernels throughout
pool_size = 2 # we will use 2x2 pooling throughout
conv_depth_1 = 32 # we will initially have 32 kernels per conv. layer...
conv_depth_2 = 64 # ...switching to 64 after the first pooling layer
drop_prob_1 = 0.25 # dropout after pooling with probability 0.25
drop_prob_2 = 0.5 # dropout in the FC layer with probability 0.5
hidden_size = 512 # the FC layer will have 512 neurons

## Loading and preprocessing the CIFAR-10 dataset is done in exactly the same way as for MNIST, with Keras routines doing most of the work. The sole difference is that now we do not initially consider each pixel an independent input feature, and therefore we do not reshape the input to 1D. We will once again force the pixel intensity values to be in the [0,1], and use a one-hot encoding for the output labels.

In [6]:
(X_train, y_train), (X_test, y_test) = cifar10.load_data() # fetch CIFAR-10 data

num_train, height, width, depth = X_train.shape # there are 50000 training examples in CIFAR-10 
num_test = X_test.shape[0] # there are 10000 test examples in CIFAR-10
num_classes = np.unique(y_train).shape[0] # there are 10 image classes

X_train = X_train.astype('float32') 
X_test = X_test.astype('float32')
X_train /= np.max(X_train) # Normalise data to [0, 1] range
X_test /= np.max(X_test) # Normalise data to [0, 1] range

Y_train = np_utils.to_categorical(y_train, num_classes) # One-hot encode the labels
Y_test = np_utils.to_categorical(y_test, num_classes) # One-hot encode the labels

In [7]:
print(num_train, height, width, depth)

50000 32 32 3


50000 32 32 3


In [8]:
inp = Input(shape=(height, width, depth)) # depth goes last in TensorFlow back-end (first in Theano)
# Conv [32] -> Conv [32] -> Pool (with dropout on the pooling layer)
conv_1 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='relu')(inp)
conv_2 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='relu')(conv_1)
pool_1 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_2)
drop_1 = Dropout(drop_prob_1)(pool_1)
# Conv [64] -> Conv [64] -> Pool (with dropout on the pooling layer)
conv_3 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='relu')(drop_1)
conv_4 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='relu')(conv_3)
pool_2 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_4)
drop_2 = Dropout(drop_prob_1)(pool_2)
# Now flatten to 1D, apply FC -> ReLU (with dropout) -> softmax
flat = Flatten()(drop_2)
hidden = Dense(hidden_size, activation='relu')(flat)
drop_3 = Dropout(drop_prob_2)(hidden)
out = Dense(num_classes, activation='softmax')(drop_3)

model = Model(inputs=inp, outputs=out) # To define a model, just specify its input and output layers

model.compile(loss='categorical_crossentropy', # using the cross-entropy loss function
              optimizer='adam', # using the Adam optimiser
              metrics=['accuracy']) # reporting the accuracy

model.fit(X_train, Y_train,                # Train the model using the training set...
          batch_size=batch_size, epochs=num_epochs,
          verbose=1, validation_split=0.1) # ...holding out 10% of the data for validation
model.evaluate(X_test, Y_test, verbose=1)  # Evaluate the trained model on the test set!

Train on 45000 samples, validate on 5000 samples
Epoch 1/2


   32/45000 [..............................] - ETA: 36:03 - loss: 2.2318 - acc: 0.1562

   64/45000 [..............................] - ETA: 22:58 - loss: 2.3956 - acc: 0.0938

   96/45000 [..............................] - ETA: 17:33 - loss: 2.3956 - acc: 0.1042

  128/45000 [..............................] - ETA: 14:53 - loss: 2.4178 - acc: 0.0938

...

 9920/10000 [============================>.] - ETA: 0s

 9952/10000 [============================>.] - ETA: 0s

 9984/10000 [============================>.] - ETA: 0s

10000/10000 [==============================] - 43s 4ms/step


[0.97364185562133787, 0.65639999999999998]

## This model achieves an accuracy of ∼78.6% on the test set; for such a difficult task (where human performance is only around 94%), and given the relative simplicity of this model, this is a respectable result. However, more sophisticated models have recently been able to get as far as 96.53%.

# Part B - Activation function (10 points)

##Q1: Change the activation function. How does it effect the accuracy?

## Answer: Change it from relu to elu(Exponential linear unit (ELU)).We could see the ELU accuracy is; 0.64834 is better a little bit than Relu. 

In [9]:
inp = Input(shape=(height, width, depth)) # depth goes last in TensorFlow back-end (first in Theano)
# Conv [32] -> Conv [32] -> Pool (with dropout on the pooling layer)
conv_1 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='elu')(inp)
conv_2 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='elu')(conv_1)
pool_1 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_2)
drop_1 = Dropout(drop_prob_1)(pool_1)
# Conv [64] -> Conv [64] -> Pool (with dropout on the pooling layer)
conv_3 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(drop_1)
conv_4 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(conv_3)
pool_2 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_4)
drop_2 = Dropout(drop_prob_1)(pool_2)
# Now flatten to 1D, apply FC -> eLU (with dropout) -> softmax
flat = Flatten()(drop_2)
hidden = Dense(hidden_size, activation='elu')(flat)
drop_3 = Dropout(drop_prob_2)(hidden)
out = Dense(num_classes, activation='softmax')(drop_3)

model = Model(inputs=inp, outputs=out) # To define a model, just specify its input and output layers

model.compile(loss='categorical_crossentropy', # using the cross-entropy loss function
              optimizer='adam', # using the Adam optimiser
              metrics=['accuracy']) # reporting the accuracy

model.fit(X_train, Y_train,                # Train the model using the training set...
          batch_size=batch_size, epochs=num_epochs,
          verbose=1, validation_split=0.1) # ...holding out 10% of the data for validation
model.evaluate(X_test, Y_test, verbose=1)  # Evaluate the trained model on the test set!

Train on 45000 samples, validate on 5000 samples
Epoch 1/2


   32/45000 [..............................] - ETA: 30:19 - loss: 2.5597 - acc: 0.0625

   64/45000 [..............................] - ETA: 18:18 - loss: 3.1334 - acc: 0.0781

   96/45000 [..............................] - ETA: 14:20 - loss: 3.1140 - acc: 0.0729

  128/45000 [..............................] - ETA: 12:22 - loss: 3.0525 - acc: 0.0859

...

 9920/10000 [============================>.] - ETA: 0s

 9952/10000 [============================>.] - ETA: 0s

 9984/10000 [============================>.] - ETA: 0s

10000/10000 [==============================] - 33s 3ms/step


[1.0109534132003783, 0.65339999999999998]

## 2. How does it effect how quickly the network plateaus?

## Answer: The speed of ELU is slower than RELU.
## The ELU: is 518s + 494s, and the RELU is 449s + 439s.

# Part C - Cost function (10 points)

## 1.Change the cost function. How does it effect the accuracy?

## Answer: Change the loss from 'cross entropy' to 'loss=losses.mean_squared_error'. The accuracy has decreased to 0.5186, 0.6126.

In [10]:
inp = Input(shape=(height, width, depth)) # depth goes last in TensorFlow back-end (first in Theano)
# Conv [32] -> Conv [32] -> Pool (with dropout on the pooling layer)
conv_1 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='elu')(inp)
conv_2 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='elu')(conv_1)
pool_1 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_2)
drop_1 = Dropout(drop_prob_1)(pool_1)
# Conv [64] -> Conv [64] -> Pool (with dropout on the pooling layer)
conv_3 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(drop_1)
conv_4 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(conv_3)
pool_2 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_4)
drop_2 = Dropout(drop_prob_1)(pool_2)
# Now flatten to 1D, apply FC -> eLU (with dropout) -> softmax
flat = Flatten()(drop_2)
hidden = Dense(hidden_size, activation='elu')(flat)
drop_3 = Dropout(drop_prob_2)(hidden)
out = Dense(num_classes, activation='softmax')(drop_3)

model = Model(inputs=inp, outputs=out) # To define a model, just specify its input and output layers

model.compile(loss='mean_squared_error', # using the mean_squared_error loss function
              optimizer='adam', # using the Adam optimiser
              metrics=['accuracy']) # reporting the accuracy

model.fit(X_train, Y_train,                # Train the model using the training set...
          batch_size=batch_size, epochs=num_epochs,
          verbose=1, validation_split=0.1) # ...holding out 10% of the data for validation
model.evaluate(X_test, Y_test, verbose=1)  # Evaluate the trained model on the test set!

Train on 45000 samples, validate on 5000 samples
Epoch 1/2


   32/45000 [..............................] - ETA: 37:50 - loss: 0.0925 - acc: 0.0312

   64/45000 [..............................] - ETA: 23:59 - loss: 0.0958 - acc: 0.0781

   96/45000 [..............................] - ETA: 19:55 - loss: 0.0993 - acc: 0.0729

  128/45000 [..............................] - ETA: 18:22 - loss: 0.0992 - acc: 0.1094

...

 9920/10000 [============================>.] - ETA: 0s

 9952/10000 [============================>.] - ETA: 0s

 9984/10000 [============================>.] - ETA: 0s

10000/10000 [==============================] - 44s 4ms/step


[0.052838684350252151, 0.60640000000000005]

## 2. How does it effect how quickly the network plateaus?

## Answer: The speed of 'mean squard error' has speeded up to 484s+450s, faster than 'Cross entropy'.

# Part D - Epochs (10 points)

## 1. Change the number of epochs initialization. How does it effect the accuracy?


## Answer: The accuracy has go up a little.
## activation function:'ELU', activation:'softmax', epoch:2, loss function: 'categorical_crossentropy':
## accuracy was 0.4342 and 0.5906
## activation function:'ELU', activation:'softmax', epoch:2, loss function: 'categorical_crossentropy': 
## accuracy was 0.5016, 0.5972, 0.6280.

In [11]:
num_epochs=3

inp = Input(shape=(height, width, depth)) # depth goes last in TensorFlow back-end (first in Theano)
# Conv [32] -> Conv [32] -> Pool (with dropout on the pooling layer)
conv_1 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='elu')(inp)
conv_2 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='elu')(conv_1)
pool_1 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_2)
drop_1 = Dropout(drop_prob_1)(pool_1)
# Conv [64] -> Conv [64] -> Pool (with dropout on the pooling layer)
conv_3 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(drop_1)
conv_4 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(conv_3)
pool_2 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_4)
drop_2 = Dropout(drop_prob_1)(pool_2)
# Now flatten to 1D, apply FC -> eLU (with dropout) -> softmax
flat = Flatten()(drop_2)
hidden = Dense(hidden_size, activation='elu')(flat)
drop_3 = Dropout(drop_prob_2)(hidden)
out = Dense(num_classes, activation='softmax')(drop_3)

model = Model(inputs=inp, outputs=out) # To define a model, just specify its input and output layers

model.compile(loss='categorical_crossentropy', # using the categorical_crossentropy loss function
              optimizer='adam', # using the Adam optimiser
              metrics=['accuracy']) # reporting the accuracy

model.fit(X_train, Y_train,                # Train the model using the training set...
          batch_size=batch_size, epochs=num_epochs,
          verbose=1, validation_split=0.1) # ...holding out 10% of the data for validation
model.evaluate(X_test, Y_test, verbose=1)  # Evaluate the trained model on the test set!

Train on 45000 samples, validate on 5000 samples
Epoch 1/3


   32/45000 [..............................] - ETA: 37:11 - loss: 2.4228 - acc: 0.0625

   64/45000 [..............................] - ETA: 23:27 - loss: 2.9988 - acc: 0.0781

   96/45000 [..............................] - ETA: 18:22 - loss: 2.9574 - acc: 0.0729

  128/45000 [..............................] - ETA: 16:08 - loss: 2.8453 - acc: 0.0703

...

 9920/10000 [============================>.] - ETA: 0s

 9952/10000 [============================>.] - ETA: 0s

 9984/10000 [============================>.] - ETA: 0s

10000/10000 [==============================] - 36s 4ms/step


[1.0268041896820068, 0.64600000000000002]

## 2. How quickly does the network plateau?

## Answer: 
## The average speed of epoch=3 is slower than epoch=2.
## (1) Speed of Activation function:'ELU', activation:'softmax', epoch:2, loss function: 'categorical_crossentropy':
## 449s+439s=888s,avg:444
## (2) Speed of activation function:'ELU', activation:'softmax', epoch:3, loss function: 'categorical_crossentropy':
## 449s+483s+461s, avg:464

# Part E - Gradient estimation (10 points)

## 1. Change the gradient estimation. How does it effect the accuracy?

## Answer:
## 1. Accuracy: optimizer='ADAM', loss='categorical_crossentropy', epoch=2: 0.4342+0.5906
## 2. Accuracy: optimizer='sgd', loss='categorical_crossentropy', epoch=2: 0.3460+0.4670

In [12]:
num_epochs=2

inp = Input(shape=(height, width, depth)) # depth goes last in TensorFlow back-end (first in Theano)
# Conv [32] -> Conv [32] -> Pool (with dropout on the pooling layer)
conv_1 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='elu')(inp)
conv_2 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='elu')(conv_1)
pool_1 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_2)
drop_1 = Dropout(drop_prob_1)(pool_1)
# Conv [64] -> Conv [64] -> Pool (with dropout on the pooling layer)
conv_3 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(drop_1)
conv_4 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(conv_3)
pool_2 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_4)
drop_2 = Dropout(drop_prob_1)(pool_2)
# Now flatten to 1D, apply FC -> eLU (with dropout) -> softmax
flat = Flatten()(drop_2)
hidden = Dense(hidden_size, activation='elu')(flat)
drop_3 = Dropout(drop_prob_2)(hidden)
out = Dense(num_classes, activation='softmax')(drop_3)

model = Model(inputs=inp, outputs=out) # To define a model, just specify its input and output layers

model.compile(loss='categorical_crossentropy', # using the categorical_crossentropy loss function
              optimizer='sgd', # Various forms of gradient estimation: using the Stochastic Gradient Descent(SGD) optimiser
              metrics=['accuracy']) # reporting the accuracy

model.fit(X_train, Y_train,                # Train the model using the training set...
          batch_size=batch_size, epochs=num_epochs,
          verbose=1, validation_split=0.1) # ...holding out 10% of the data for validation
model.evaluate(X_test, Y_test, verbose=1)  # Evaluate the trained model on the test set!

Train on 45000 samples, validate on 5000 samples
Epoch 1/2


   32/45000 [..............................] - ETA: 27:27 - loss: 2.3812 - acc: 0.1562

   64/45000 [..............................] - ETA: 18:08 - loss: 2.3636 - acc: 0.1406

   96/45000 [..............................] - ETA: 14:25 - loss: 2.3396 - acc: 0.1354

  128/45000 [..............................] - ETA: 12:18 - loss: 2.3222 - acc: 0.1328

...

 9920/10000 [============================>.] - ETA: 0s

 9952/10000 [============================>.] - ETA: 0s

 9984/10000 [============================>.] - ETA: 0s

10000/10000 [==============================] - 34s 3ms/step


[1.3280842678070068, 0.53010000000000002]

## 2. How does it effect how quickly the network plateaus?

## Answer: 
## 1. Speed of optimizer='ADAM', loss='categorical_crossentropy', epoch=2: 449s+439s

## 2. Speed of optimizer='SPG', loss='categorical_crossentropy', epoch=2: 471s+422s

# Part F - Network Architecture

## 1. Change the network architecture. How does it effect the accuracy?
## Number of layers

##Answer:
## 1. Layer=3: 0.3548+0.4740 is more accurate than 2 layers.
## 2. Layer=2: 0.3460+0.4670

In [13]:
batch_size = 32 
num_epochs = 2 
kernel_size = 4 # Change 3*3 to 4*4 filter.
pool_size = 2 
conv_depth_1 = 32
conv_depth_2 = 64 
drop_prob_1 = 0.25 
drop_prob_2 = 0.5 
hidden_size = 512 

inp = Input(shape=(height, width, depth)) # depth goes last in TensorFlow back-end (first in Theano)
# Conv [32] -> Conv [32] -> Pool (with dropout on the pooling layer)
conv_1 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='elu')(inp)
conv_2 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='elu')(conv_1)

pool_1 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_2)
drop_1 = Dropout(drop_prob_1)(pool_1)
# Conv [64] -> Conv [64] -> Pool (with dropout on the pooling layer)

conv_3 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(drop_1)
conv_4 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(conv_3)

pool_2 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_4)
drop_2 = Dropout(drop_prob_1)(pool_2)

#!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!Add more layer here:
conv_5 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(drop_2)
conv_6 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='elu')(conv_5)

pool_3 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_6)
drop_3 = Dropout(drop_prob_1)(pool_3)

# Now flatten to 1D, apply FC -> eLU (with dropout) -> softmax
flat = Flatten()(drop_3)
hidden = Dense(hidden_size, activation='elu')(flat)
drop_3 = Dropout(drop_prob_2)(hidden)

out = Dense(num_classes, activation='softmax')(drop_3)

model = Model(inputs=inp, outputs=out) # To define a model, just specify its input and output layers

model.compile(loss='categorical_crossentropy', # using the categorical_crossentropy loss function
              optimizer='sgd', # Various forms of gradient estimation: using the Stochastic Gradient Descent(SGD) optimiser
              metrics=['accuracy']) # reporting the accuracy

model.fit(X_train, Y_train,                # Train the model using the training set...
          batch_size=batch_size, epochs=num_epochs,
          verbose=1, validation_split=0.1) # ...holding out 10% of the data for validation
model.evaluate(X_test, Y_test, verbose=1)  # Evaluate the trained model on the test set!

Train on 45000 samples, validate on 5000 samples
Epoch 1/2


   32/45000 [..............................] - ETA: 58:00 - loss: 2.3854 - acc: 0.0938

   64/45000 [..............................] - ETA: 39:52 - loss: 2.3454 - acc: 0.1562

   96/45000 [..............................] - ETA: 32:41 - loss: 2.3244 - acc: 0.1250

  128/45000 [..............................] - ETA: 28:48 - loss: 2.3305 - acc: 0.1172

...

 9920/10000 [============================>.] - ETA: 0s

 9952/10000 [============================>.] - ETA: 0s

 9984/10000 [============================>.] - ETA: 0s

10000/10000 [==============================] - 63s 6ms/step


[1.3255888254165649, 0.51429999999999998]

## 2. How does it effect how quickly the network plateaus?
## Answer: The speed of Layers 3 is slower than Layer 2.
## Layer=2: Speed=471s+422s=893s
## Layer=3: Speed=500s+691s=1191s

# Part G - Network initialization (10 points)

## Various forms of network initialization(Different layer types might have different default kernel_initializer.):
## 0
## Uniform
## Gaussian(Mostly default)
## Xavier Glorot Initialization http://andyljones.tumblr.com/post/110998971763/an-explanation-of-xavier-initialization
## Xavier Uniform（we need to initialize the weights in such a way that the variance remains the same for x and y. This initialization process is known as Xavier initialization.）
## Xavier Gaussian

## 1. Change the network initialization. How does it effect the accuracy?
## Answer: 
## Change to Gaussian( for kernel initialization, the accuracy is 0.4450, 0.6081 is better than the default initialization.
## Compared with the default: 0.4342, 0.5906

In [44]:
from keras import initializers

In [14]:
batch_size = 32 # in each iteration, we consider 32 training examples at once
num_epochs = 2 # we iterate 200 times over the entire training set
kernel_size = 3 # we will use 3x3 kernels throughout
pool_size = 2 # we will use 2x2 pooling throughout
conv_depth_1 = 32 # we will initially have 32 kernels per conv. layer...
conv_depth_2 = 64 # ...switching to 64 after the first pooling layer
drop_prob_1 = 0.25 # dropout after pooling with probability 0.25
drop_prob_2 = 0.5 # dropout in the FC layer with probability 0.5
hidden_size = 512 # the FC layer will have 512 neurons

inp = Input(shape=(height, width, depth)) # depth goes last in TensorFlow back-end (first in Theano)
# Conv [32] -> Conv [32] -> Pool (with dropout on the pooling layer)
conv_1 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='relu')(inp)
conv_2 = Convolution2D(conv_depth_1, (kernel_size, kernel_size), padding='same', activation='relu')(conv_1)
pool_1 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_2)
drop_1 = Dropout(drop_prob_1)(pool_1)
# Conv [64] -> Conv [64] -> Pool (with dropout on the pooling layer)
conv_3 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='relu')(drop_1)
conv_4 = Convolution2D(conv_depth_2, (kernel_size, kernel_size), padding='same', activation='relu')(conv_3)
pool_2 = MaxPooling2D(pool_size=(pool_size, pool_size))(conv_4)
drop_2 = Dropout(drop_prob_1)(pool_2)
# Now flatten to 1D, apply FC -> ReLU (with dropout) -> softmax
flat = Flatten()(drop_2)

hidden = Dense(hidden_size, 
               kernel_initializer='random_normal', #!!!!!!!!!!!!!!!!!!!!!!!!!!!!!! Called 'Gaussian' also.
               bias_initializer='zeros',activation='relu')(flat)

drop_3 = Dropout(drop_prob_2)(hidden)

out = Dense(num_classes, activation='softmax')(drop_3)

model = Model(inputs=inp, outputs=out) # To define a model, just specify its input and output layers

# model.add(Dense(64,
#                 kernel_initializer='random_normal',
#                 bias_initializer='zeros'))

model.compile(loss='categorical_crossentropy', # using the cross-entropy loss function
              optimizer='adam', # using the Adam optimiser
              metrics=['accuracy']) # reporting the accuracy

model.fit(X_train, Y_train,                # Train the model using the training set...
          batch_size=batch_size, epochs=num_epochs,
          verbose=1, validation_split=0.1) # ...holding out 10% of the data for validation
model.evaluate(X_test, Y_test, verbose=1)  # Evaluate the trained model on the test set!



Train on 45000 samples, validate on 5000 samples
Epoch 1/2


   32/45000 [..............................] - ETA: 38:37 - loss: 2.3180 - acc: 0.1250

   64/45000 [..............................] - ETA: 23:46 - loss: 2.4035 - acc: 0.1094

   96/45000 [..............................] - ETA: 18:46 - loss: 2.3837 - acc: 0.0938

  128/45000 [..............................] - ETA: 16:04 - loss: 2.3997 - acc: 0.1016

...

43392/45000 [===========================>..] - ETA: 20s - loss: 1.1245 - acc: 0.5990

43424/45000 [===========================>..] - ETA: 20s - loss: 1.1244 - acc: 0.5990

43456/45000 [===========================>..] - ETA: 19s - loss: 1.1243 - acc: 0.5991

43488/45000 [===========================>..] - ETA: 19s - loss: 1.1241 - acc: 0.5992

43520/45000 [============================>.] - ETA: 19s - loss: 1.1239 - acc: 0.5992

## 2. How does it effect how quickly the network plateaus?
## Answer: The spped with Gaussian(Random normal) is 508s+443s, which is slower than the previous one.
## Compared with the default one: 449s+439s